
# IDF-based MDO on the Sobieski SSBJ test case


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo import generate_n2_plot
from gemseo.problems.sobieski.core.design_space import SobieskiDesignSpace

configure_logger()

## Instantiate the  disciplines
First, we instantiate the four disciplines of the use case:
:class:`.SobieskiPropulsion`,
:class:`.SobieskiAerodynamics`,
:class:`.SobieskiMission`
and :class:`.SobieskiStructure`.



In [ ]:
disciplines = create_discipline([
    "SobieskiPropulsion",
    "SobieskiAerodynamics",
    "SobieskiMission",
    "SobieskiStructure",
])

We can quickly access the most relevant information of any discipline (name, inputs,
and outputs) with Python's ``print()`` function. Moreover, we can get the default
input values of a discipline with the attribute :attr:`.MDODiscipline.default_inputs`



In [ ]:
for discipline in disciplines:
    print(discipline)
    print(f"Default inputs: {discipline.default_inputs}")

You may also be interested in plotting the couplings of your disciplines.
A quick way of getting this information is the API function
:func:`.generate_n2_plot`. A much more detailed explanation of coupling
visualization is available `here <coupling_visualization>`.



In [ ]:
generate_n2_plot(disciplines, save=False, show=True)

## Build, execute and post-process the scenario
Then, we build the scenario which links the disciplines
with the formulation and the optimization algorithm. Here, we use the
:class:`.IDF` formulation. We tell the scenario to minimize -y_4 instead of
minimizing y_4 (range), which is the default option.

### Instantiate the scenario



In [ ]:
design_space = SobieskiDesignSpace()
design_space

In [ ]:
scenario = create_scenario(
    disciplines,
    "IDF",
    "y_4",
    design_space,
    maximize_objective=True,
)

### Set the design constraints



In [ ]:
for c_name in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(c_name, constraint_type="ineq")

### Visualize the XDSM
Generate the XDSM file on the fly:

- ``log_workflow_status=True`` will log the status of the workflow  in the console,
- ``save_html`` (default ``True``) will generate a self-contained HTML file,
  that can be automatically opened using ``show_html=True``.



In [ ]:
scenario.xdsmize(save_html=False)

### Define the algorithm inputs
We set the maximum number of iterations, the optimizer
and the optimizer options



In [ ]:
algo_options = {
    "ftol_rel": 1e-10,
    "ineq_tolerance": 1e-3,
    "eq_tolerance": 1e-3,
    "normalize_design_space": True,
}
scn_inputs = {"max_iter": 20, "algo": "SLSQP", "algo_options": algo_options}

### Execute the scenario



In [ ]:
scenario.execute(scn_inputs)

### Save the optimization history
We can save the whole optimization problem and its history for further post
processing:



In [ ]:
scenario.save_optimization_history("idf_history.h5", file_format="hdf5")

We can also save only calls to functions and design variables history:



In [ ]:
scenario.save_optimization_history("idf_history.xml", file_format="ggobi")

### Print optimization metrics



In [ ]:
scenario.print_execution_metrics()

### Plot the optimization history view



In [ ]:
scenario.post_process("OptHistoryView", save=True, show=True)

### Plot the quadratic approximation of the objective



In [ ]:
scenario.post_process("QuadApprox", function="-y_4", save=False, show=True)